Лабораторная работа 3. Спасюк Мария, Родионцева Ирина 22ПМИ1

In [2]:
!pip install xgboost --upgrade

In [380]:
!pip install ydata-profiling

  Using cached visions-0.7.6-py3-none-any.whl.metadata (11 kB)
  Using cached multimethod-1.12-py3-none-any.whl.metadata (9.6 kB)
  Using cached dacite-1.8.1-py3-none-any.whl.metadata (15 kB)
   ---------------------------------------- 0.0/390.9 kB ? eta -:--:--
   --- ------------------------------------ 30.7/390.9 kB 1.4 MB/s eta 0:00:01
   ----------- ---------------------------- 112.6/390.9 kB 1.3 MB/s eta 0:00:01
   ----------------------- ---------------- 225.3/390.9 kB 1.7 MB/s eta 0:00:01
   ---------------------------------- ----- 337.9/390.9 kB 2.1 MB/s eta 0:00:01
   ---------------------------------------- 390.9/390.9 kB 2.0 MB/s eta 0:00:00
Using cached dacite-1.8.1-py3-none-any.whl (14 kB)
Using cached multimethod-1.12-py3-none-any.whl (10 kB)
Using cached visions-0.7.6-py3-none-any.whl (104 kB)
   ---------------------------------------- 0.0/301.2 kB ? eta -:--:--
   ---------------------------------------- 301.2/301.2 kB 9.1 MB/s eta 0:00:00
  Attempting uninstall: mult

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pandas-profiling 3.2.0 requires visions[type_image_path]==0.7.4, but you have visions 0.7.6 which is incompatible.


In [580]:
import pandas as pd
import os
import numpy as np
from matplotlib import pylab as plot
%pylab inline

import xgboost as xgb
from xgboost.sklearn import XGBClassifier
from ydata_profiling import ProfileReport

%pylab is deprecated, use %matplotlib inline and import the required libraries.
Populating the interactive namespace from numpy and matplotlib


c:\Users\PCUserName\anaconda3\Lib\site-packages\IPython\core\magics\pylab.py:166: UserWarning: pylab import has clobbered these variables: ['plot']
`%matplotlib` prevents importing * from pylab and numpy
  warn("pylab import has clobbered these variables: %s"  % clobbered +


Загружаем данные

In [581]:
x_train = pd.read_csv('train.csv')
x_test = pd.read_csv('test.csv')
passenger_id = x_test['PassengerId']

In [582]:
x_train

PassengerId HomePlanet CryoSleep     Cabin    Destination   Age    VIP  \
0        0001_01     Europa     False     B/0/P    TRAPPIST-1e  39.0  False   
1        0002_01      Earth     False     F/0/S    TRAPPIST-1e  24.0  False   
2        0003_01     Europa     False     A/0/S    TRAPPIST-1e  58.0   True   
3        0003_02     Europa     False     A/0/S    TRAPPIST-1e  33.0  False   
4        0004_01      Earth     False     F/1/S    TRAPPIST-1e  16.0  False   
...          ...        ...       ...       ...            ...   ...    ...   
8688     9276_01     Europa     False    A/98/P    55 Cancri e  41.0   True   
8689     9278_01      Earth      True  G/1499/S  PSO J318.5-22  18.0  False   
8690     9279_01      Earth     False  G/1500/S    TRAPPIST-1e  26.0  False   
8691     9280_01     Europa     False   E/608/S    55 Cancri e  32.0  False   
8692     9280_02     Europa     False   E/608/S    TRAPPIST-1e  44.0  False   

      RoomService  FoodCourt  ShoppingMall     Spa  VRDeck               Name  \
0             0.0        0.0           0.0     0.0     0.0    Maham Ofracculy   
1           109.0        9.0          25.0   549.0    44.0       Juanna Vines   
2            43.0     3576.0           0.0  6715.0    49.0      Altark Susent   
3             0.0     1283.0         371.0  3329.0   193.0       Solam Susent   
4           303.0       70.0         151.0   565.0     2.0  Willy Santantines   
...           ...        ...           ...     ...     ...                ...   
8688          0.0     6819.0           0.0  1643.0    74.0  Gravior Noxnuther   
8689          0.0        0.0           0.0     0.0     0.0    Kurta Mondalley   
8690          0.0        0.0        1872.0     1.0     0.0       Fayey Connon   
8691          0.0     1049.0           0.0   353.0  3235.0   Celeon Hontichre   
8692        126.0     4688.0           0.0     0.0    12.0   Propsh Hontichre   

      Transported  
0           False  
1            True  
2           False  
3           False  
4            True  
...           ...  
8688        False  
8689        False  
8690         True  
8691        False  
8692         True  

[8693 rows x 14 columns]

Выполним анализ имеющихся данных в train по пассажирам. Посмотрим, как переменные зависят друг от друга и как влияют на целевую переменную.

In [583]:
ProfileReport(x_train)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

По матрице корреляций можем заметить, что переменные Transported и Cryosleep имеют достаточно сильную связь. 

Скопируем колонку Transported в y_train

In [584]:
y_train = x_train['Transported']

In [585]:
try:
    x_train = x_train.drop(['Transported'], axis = 1)
except:
    print("column not found")

Посмотрим, какие типы переменных присутствуют в датасете

In [586]:
x_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   8693 non-null   object 
 1   HomePlanet    8492 non-null   object 
 2   CryoSleep     8476 non-null   object 
 3   Cabin         8494 non-null   object 
 4   Destination   8511 non-null   object 
 5   Age           8514 non-null   float64
 6   VIP           8490 non-null   object 
 7   RoomService   8512 non-null   float64
 8   FoodCourt     8510 non-null   float64
 9   ShoppingMall  8485 non-null   float64
 10  Spa           8510 non-null   float64
 11  VRDeck        8505 non-null   float64
 12  Name          8493 non-null   object 
dtypes: float64(6), object(7)
memory usage: 883.0+ KB


Разделим колонку Cabin на 3 новые (Deck, Cabin_number, Side)

In [587]:
x_train[["Deck", "CabinNumber", "Side"]] = x_train["Cabin"].str.split("/", expand=True)
x_test[["Deck", "CabinNumber", "Side"]] = x_test["Cabin"].str.split("/", expand=True)
try:
    x_train = x_train.drop('Cabin', axis=1)
except KeyError:
    print("Field does not exist")
try:
    x_test = x_test.drop('Cabin', axis=1)
except KeyError:
    print("Field does not exist")


Посчитаем все траты каждого пассажира и вынесем их в отдельную колонку

In [588]:
x_train['all_costs'] = x_train['RoomService'] + x_train['FoodCourt'] + x_train['ShoppingMall'] + x_train['Spa'] + x_train['VRDeck']
x_test['all_costs'] = x_test['RoomService'] + x_test['FoodCourt'] + x_test['ShoppingMall'] + x_test['Spa'] + x_test['VRDeck']

In [589]:
x_train.head(5)

PassengerId HomePlanet CryoSleep  Destination   Age    VIP  RoomService  \
0     0001_01     Europa     False  TRAPPIST-1e  39.0  False          0.0   
1     0002_01      Earth     False  TRAPPIST-1e  24.0  False        109.0   
2     0003_01     Europa     False  TRAPPIST-1e  58.0   True         43.0   
3     0003_02     Europa     False  TRAPPIST-1e  33.0  False          0.0   
4     0004_01      Earth     False  TRAPPIST-1e  16.0  False        303.0   

   FoodCourt  ShoppingMall     Spa  VRDeck               Name Deck  \
0        0.0           0.0     0.0     0.0    Maham Ofracculy    B   
1        9.0          25.0   549.0    44.0       Juanna Vines    F   
2     3576.0           0.0  6715.0    49.0      Altark Susent    A   
3     1283.0         371.0  3329.0   193.0       Solam Susent    A   
4       70.0         151.0   565.0     2.0  Willy Santantines    F   

  CabinNumber Side  all_costs  
0           0    P        0.0  
1           0    S      736.0  
2           0    S    10383.0  
3           0    S     5176.0  
4           1    S     1091.0

Для каждого столбца проверим наличие NaN

In [590]:
x_train.isna().sum()

PassengerId       0
HomePlanet      201
CryoSleep       217
Destination     182
Age             179
VIP             203
RoomService     181
FoodCourt       183
ShoppingMall    208
Spa             183
VRDeck          188
Name            200
Deck            199
CabinNumber     199
Side            199
all_costs       908
dtype: int64

Характеристики PassengerID и Name не несут смысла для обучения модели, поэтому удалим их. Также номер каюты может спутать модель, так как каюты с одинаковым номером присутствуют при разных данных в колонках Deck и Side, из чего можно предположить, что эти 2 характеристики имеют большее влияние, чем CabinNumber

In [591]:
try:
    x_train = x_train.drop(['CabinNumber','PassengerId', 'Name'], axis = 1)
except:
    print("Column not found")
try:
    x_test = x_test.drop(['CabinNumber','PassengerId', 'Name'], axis = 1)
except:
    print("Column not found")

In [592]:
x_test.isna().sum()

HomePlanet       87
CryoSleep        93
Destination      92
Age              91
VIP              93
RoomService      82
FoodCourt       106
ShoppingMall     98
Spa             101
VRDeck           80
Deck            100
Side            100
all_costs       455
dtype: int64

Продолжим выполнять предобработку данных. Закодируем категориальные признаки, заполним пропуски и нормализуем данные

In [593]:
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import MinMaxScaler,StandardScaler

In [594]:
def prepare(a):
    a['Age'] = a['Age'].fillna(a['Age'].mode()[0])
    a['HomePlanet'] = a['HomePlanet'].fillna("not_clear")
    a['Destination'] = a['Destination'].fillna("not_clear")
    a['Deck'] = a['Deck'].fillna("not_clear")
    a['Side'] = a['Side'].fillna("not_clear")
    a['CryoSleep'] = a['CryoSleep'].fillna("False")
    a['VIP'] = a['VIP'].fillna('False')
    a['VRDeck'] = a['VRDeck'].fillna(0)
    a['RoomService'] = a['RoomService'].fillna(0)
    a['FoodCourt'] = a['FoodCourt'].fillna(0)
    a['ShoppingMall'] = a['ShoppingMall'].fillna(0)
    a['Spa'] = a['Spa'].fillna(0)
    a['all_costs'] = a['all_costs'].fillna(0)
    return a

In [595]:
x_train = prepare(x_train)
x_test = prepare(x_test)

In [596]:
num_features = ['Age','RoomService','FoodCourt','ShoppingMall','Spa','VRDeck','all_costs']

from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
train_num_scaled = scaler.fit_transform(x_train[num_features])
test_num_scaled = scaler.transform(x_test[num_features])

train_num_scaled = pd.DataFrame(data=train_num_scaled,columns=num_features)
test_num_scaled = pd.DataFrame(data=test_num_scaled,columns=num_features)

# кодирование категориальных переменных
cat_features = ['HomePlanet','CryoSleep','Destination','VIP','Deck','Side']

train_cat_encoded = pd.get_dummies(x_train[cat_features],drop_first=True)
test_cat_encoded = pd.get_dummies(x_test[cat_features],drop_first=True)

In [597]:
x_train = pd.concat([train_num_scaled,train_cat_encoded],axis=1)
x_test = pd.concat([test_num_scaled,test_cat_encoded],axis=1)


Выполним разделение датасета train на тренировочную и тестовую выборки, чтобы потом отслеживать accuracy на тесте

In [598]:
from sklearn.model_selection import train_test_split
np.random.seed(3)
x_train_small, x_test_small, y_train_small, y_test_small = train_test_split(x_train, y_train, test_size=0.3, random_state=7)

In [600]:
x_train.head()

Age  RoomService  FoodCourt  ShoppingMall       Spa    VRDeck  \
0  0.493671     0.000000   0.000000      0.000000  0.000000  0.000000   
1  0.303797     0.007608   0.000302      0.001064  0.024500  0.001823   
2  0.734177     0.003001   0.119948      0.000000  0.299670  0.002030   
3  0.417722     0.000000   0.043035      0.015793  0.148563  0.007997   
4  0.202532     0.021149   0.002348      0.006428  0.025214  0.000083   

   all_costs  HomePlanet_Europa  HomePlanet_Mars  HomePlanet_not_clear  ...  \
0   0.000000               True            False                 False  ...   
1   0.020452              False            False                 False  ...   
2   0.288521               True            False                 False  ...   
3   0.143830               True            False                 False  ...   
4   0.030317              False            False                 False  ...   

   Deck_B  Deck_C  Deck_D  Deck_E  Deck_F  Deck_G  Deck_T  Deck_not_clear  \
0    True   False   False   False   False   False   False           False   
1   False   False   False   False    True   False   False           False   
2   False   False   False   False   False   False   False           False   
3   False   False   False   False   False   False   False           False   
4   False   False   False   False    True   False   False           False   

   Side_S  Side_not_clear  
0   False           False  
1    True           False  
2    True           False  
3    True           False  
4    True           False  

[5 rows x 27 columns]

In [601]:
x_test.head()

Age  RoomService  FoodCourt  ShoppingMall       Spa    VRDeck  \
0  0.341772     0.000000   0.000000       0.00000  0.000000  0.000000   
1  0.240506     0.000000   0.000302       0.00000  0.125982  0.000000   
2  0.392405     0.000000   0.000000       0.00000  0.000000  0.000000   
3  0.481013     0.000000   0.223124       0.00000  0.008077  0.024241   
4  0.253165     0.000698   0.000000       0.02703  0.000000  0.000000   

   all_costs  HomePlanet_Europa  HomePlanet_Mars  HomePlanet_not_clear  ...  \
0   0.000000              False            False                 False  ...   
1   0.078695              False            False                 False  ...   
2   0.000000               True            False                 False  ...   
3   0.206130               True            False                 False  ...   
4   0.017923              False            False                 False  ...   

   Deck_B  Deck_C  Deck_D  Deck_E  Deck_F  Deck_G  Deck_T  Deck_not_clear  \
0   False   False   False   False   False    True   False           False   
1   False   False   False   False    True   False   False           False   
2   False    True   False   False   False   False   False           False   
3   False    True   False   False   False   False   False           False   
4   False   False   False   False    True   False   False           False   

   Side_S  Side_not_clear  
0    True           False  
1    True           False  
2    True           False  
3    True           False  
4    True           False  

[5 rows x 27 columns]

Приступим к реализации модели. Будем использовать Catboost для предсказания результата. 


In [602]:
pip install catboost

Note: you may need to restart the kernel to use updated packages.


In [603]:
from catboost import CatBoostClassifier
model = CatBoostClassifier(
    learning_rate=0.05,
    iterations=300,
    random_seed=43,
    custom_loss=['AUC', 'Accuracy'],
    depth = 5
)

In [605]:
model.fit(
    x_train_small, y_train_small,
    eval_set=(x_test_small, y_test_small),
    verbose=False,
    plot=True
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [606]:
y_pred_small = model.predict(x_test_small)

Посчитаем accuracy на тестовой выборке из датасета train

In [607]:
from sklearn.metrics import accuracy_score
print(accuracy_score(y_test_small, y_pred_small))

0.8163343558282209


Обучим модель на полных данных и предскажем значения столбца Transported для датасета test. Запишем результаты в файл sample_submission

In [608]:
model.fit(
    x_train, y_train,
    verbose=False,
    plot=True
)
y_pred = model.predict(x_test)
results = pd.DataFrame()
results['PassengerId'] = passenger_id
results['Transported'] = y_pred
results['Transported'] = results['Transported'].astype(bool)
results.to_csv('sample_submission.csv', index = False)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))